Reference
===

1. FB權限問題，無法訪問資料庫(解決)<br> 
[Object with ID '203618703567212' does not exist, cannot be loaded due to missing permissions, or does not support this operation](https://stackoverflow.com/questions/50266800/object-with-id-203618703567212-does-not-exist-cannot-be-loaded-due-to-missing)

需要金鑰權限重新設定<br>

2. 



In [ ]:
from facebook_business.adobjects.adaccount import AdAccount
from facebook_business.adobjects.adsinsights import AdsInsights
from facebook_business.api import FacebookAdsApi
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
import csv
import time

# 起始值
"""
access_token: 廣告金鑰
ad_account_id: 廣告帳戶
data_back: 回溯(幾個月)爬資料
fields: FB_Ads行銷廣告資料
"""
# Initial Values
# 舊的金鑰
access_token = 'EAAJqMzKi2IsBAJp9LxmjKZBfEG5P5WXqzUO8f4eXoUYRr9beYIxSRXKFuXMUTVZCMaJnwewurtWpq93qiyB7X8wfDotZCQZC5M1B9YZAgIuiTEY5cHgOZAhmxGpOin6DM0HZAPcAmzs8YDBnAs4YzS9D1D5jZCLWLUkdhGVhbmddkAZDZD'
ad_account_id = 'act_132799196821088'
data_back = 6

FacebookAdsApi.init(access_token = access_token)

# Insight API中的fields資料(控制需要的欄位資料)
fields = [
    'spend',
    'campaign_name',
    'adset_name',
    'campaign_id',
    'actions',
    'objective',
    'action_values',  
    'conversions',
    'conversion_values',
]

# 日期計算
def original_time():
    """
    a_week: 一星期
    a_day: 一天
    end_time: 回推月份 - 1個月
    start_time: 回推月份
    """
    a_week = relativedelta(weeks = 1)
    a_day = relativedelta(days = 1)
    
    # 回推月份
    start_time = datetime.now() - data_back*relativedelta(months = 1)
    # 回推月份 - 1個月
    end_time = datetime.now() - (data_back-1)*relativedelta(months = 1)
    return start_time, end_time

# 計算程式共跑幾次
begin_count = 0
# 起始時間和結束時間(1次1個月)
start_time, end_time = original_time()

# 建立CSV資料，並將Business SDK獲得的資料儲存
outfn_t = '{}_fb.txt'.format(datetime.now().strftime('%Y-%m-%d') + '123FB_Ads_Marketing_Data')

title_row = ['Campaign_name' + '\t' + 'Objective' + '\t' + \
             'Amount_spent(NTD)' + '\t' + 'Amount_install'  + '\t' +\
             'Amount_purchase' + '\t' + 'Purchase_Conversion_Value'  + '\t' +\
             'Amount_subscribe' + '\t' + 'Subscribe_Conversion_Value' + '\t' +\
             'Reporting_date']

with open(outfn_t, 'w', encoding = 'utf-8') as textout:
        textout.write(','.join(title_row) + '\n')

# 紀錄程式跑多久時間
run_time = time.time()
    
# 開始將資料一個月一個月寫入資料庫
for i in range(data_back):
    # Insight API中的fields資料(控制日期條件、資料的層級)
    params = {
        'time_range': {
                    'since': start_time.strftime('%Y-%m-%d'),\
                    'until': end_time.strftime('%Y-%m-%d') 
        }, 

        'level': {'campaign'},
        'time_increment': '1',

        # Default 歸因(目前確認和廣告面板上面的相同 7天點擊 + 7天瀏覽)
        # 'use_account_attribution_setting': 'True',

        # 手動設定的歸因: 7天點擊後(和廣告預設值有落差)
        'action_attribution_windows': {'7d_click'},
    }

    acc_insights = AdAccount(ad_account_id).get_insights(
        fields = fields,
        params = params,
    )
    
    with open(outfn_t, 'a', encoding = 'utf-8') as textout:
        start_time = start_time + relativedelta(months = 1, days = 1)
        end_time = end_time + relativedelta(months = 1)
        
        for acc_insight in acc_insights:     
            Campaign_name = ''
            Amount_spent = ''
            Objective = ''
            Amount_subscribe = '' 
            Subscribe_Conversion_Value = ''
            Amount_install = '' 
            Amount_purchase = ''    
            Purchase_Conversion_Value = ''
            Reporting_date = ''
        
            # insights/campaign_name得到 "產品包名稱"
            if 'campaign_name' in acc_insight:
                Campaign_name = acc_insight['campaign_name']
                if '⛔️股市爆料同學會' in Campaign_name:
                    Campaign_name = Campaign_name.replace('⛔️', '').strip()
                        
            # insights/spend得到 "總支出成本"
            if 'spend' in acc_insight:    
                Amount_spent = acc_insight['spend']

            # insights/objective得到 "廣告目標"
            if 'objective' in acc_insight:
                Objective = acc_insight['objective']

            # insights/date_stop得到 "報表終止日期"
            if 'date_stop' in acc_insight:
                Reporting_date = acc_insight['date_stop']

            # insights/actions得到 "軟體下載數/課程購買數"
            if 'actions' in acc_insight:
                for action in acc_insight['actions']:
                    if action['action_type'] == 'mobile_app_install': 
                        Amount_install = action['value']
                    if action['action_type'] == 'purchase':
                        Amount_purchase = action['value']

            # insights/action_values得到 "購買轉換價值"
            if 'action_values' in acc_insight:
                for ac_values in acc_insight['action_values']:
                    if ac_values['action_type'] == 'omni_purchase':
                        Purchase_Conversion_Value = ac_values['value']

            # insights/conversions得到 "訂閱數"
            if 'conversions' in acc_insight:
                for cv in acc_insight['conversions']:
                    if cv['action_type'] == 'subscribe_total':
                        try:
                            Amount_subscribe = cv['7d_click']
                        except:
                            Amount_subscribe = cv['value']

            # insights/conversion_values得到 "訂閱轉換價值"             
            if 'conversion_values' in acc_insight:
                for cv_values in acc_insight['conversion_values']:
                    if cv_values['action_type'] == 'subscribe_total':
                        try:
                            Subscribe_Conversion_Value = cv_values['7d_click']
                        except:
                            Subscribe_Conversion_Value = cv_values['value']
            
            # 資料以間格方式儲存於text檔案
            try:
                stuff = [Campaign_name + '\t' + Objective + '\t' + Amount_spent \
                         + '\t' + Amount_install + '\t' + Amount_purchase\
                         + '\t' + Purchase_Conversion_Value + '\t' + Amount_subscribe\
                         + '\t' + Subscribe_Conversion_Value + '\t' + Reporting_date]
                textout.write(','.join(stuff) + '\n')
            except UnicodeEncodeError as e:
                print(e)
                textout.write(' ' + '\n')
           
        print('第{}次'.format(i)) 
        time.sleep(100)

# flag確立program完整結束
print('--- %s seconds ---' % (time.time() - run_time))

In [ ]:
from facebook_business.adobjects.adaccount import AdAccount
from facebook_business.adobjects.adsinsights import AdsInsights
from facebook_business.api import FacebookAdsApi
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
import csv
import time
import pandas as pd
import pyodbc


# Initialize the access_token
# 新的金鑰
access_token = 'EAAJqMzKi2IsBAGoi5I6pSy5VgdsWQr9LfZB9c9JYrjq28AjDJbw8kE1repJSYDAvmNf5vJh0kVQF5Fzh98VJyzCNJat1OkHSqIBKZA9hLA6iVvKKH4Bwa9TU36p72DP1cOAZBhHkq5UbXGLmZB7K36frR2OhZBRdILoeCrZCA2AOd8RkSvJ1sGsekXTOd7xMAZD'
ad_account_id = 'act_132799196821088'
app_secret = 'b3700e4944af0e889dc572179bd6800d'
app_id = '679718078830731'
FacebookAdsApi.init(access_token = access_token)

# Insight API中的fields資料(控制需要的欄位資料)
fields = [
    'spend',
    'campaign_name',
    'adset_name',
    'campaign_id',
    'actions',
    'objective',
    'action_values',  
    'conversions',
    'conversion_values',
]

week_add = relativedelta(weeks = 1)
day_add = relativedelta(days = 1)

# 回溯到6個月以前，定義data_back = 6
data_back = 6

# 現在時間回推7天
end_time = datetime.now() - (data_back - 1)*relativedelta(months = 1)
# 從甚麼時候
start_time = datetime.now() - data_back*relativedelta(months = 1)
begin_count = 0

# 建立CSV資料，並將Business SDK獲得的資料儲存
outfn_t = '{}.txt'.format('Test_FB_Ads_Marketing_Data')


title_row = ['Campaign_name' + '\t' + 'Objective' + '\t' + \
             'Amount_spent(NTD)' + '\t' + 'Amount_install'  + '\t' +\
             'Amount_purchase' + '\t' + 'Purchase_Conversion_Value'  + '\t' +\
             'Amount_subscribe' + '\t' + 'Subscribe_Conversion_Value' + '\t' +\
             'Reporting_date']

with open(outfn_t, 'w', encoding = 'utf-8') as textout:
        textout.write(','.join(title_row) + '\n')


# 開始將資料一個月一個月寫入資料庫
for i in range(data_back):
    # Insight API中的fields資料(控制日期條件、資料的層級)
    params = {
        'time_range': {
                    'since': start_time.strftime('%Y-%m-%d'),\
                    'until': end_time.strftime('%Y-%m-%d') 
        }, 

        'level': {'campaign'},
        'time_increment': '1',

        # Default 歸因(目前確認和廣告面板上面的相同 7天點擊 + 7天瀏覽)
        # 'use_account_attribution_setting': 'True',

        # 自己設定的歸因(和廣告預設值有落差)
        'action_attribution_windows': {'7d_click'},
    }

    acc_insights = AdAccount(ad_account_id).get_insights(
        fields = fields,
        params = params,
    )

    # 寫入資料庫-----------------------------------------------------
    run_time = time.time()
    # 原始紀錄值
    order = 0

#     with open(outfn, 'a', newline = '') as csvout:
#         csvWriter = csv.writer(csvout)
    with open(outfn_t, 'a', encoding = 'utf-8') as textout:
        
        start_time = start_time + day_add + relativedelta(months = 1)
        end_time = end_time + relativedelta(months = 1)
        
        for acc_insight in acc_insights:
            Campaign_name = ''
            Amount_spent = ''
            Objective = ''
            Amount_subscribe = '' 
            Subscribe_Conversion_Value = ''
            Amount_install = '' 
            Amount_purchase = ''    
            Purchase_Conversion_Value = ''
            Reporting_date = ''
            
            # 紀錄值+1
            order += 1
            
            # insights/campaign_name得到 "產品包名稱"
            if 'campaign_name' in acc_insight:
                Campaign_name = acc_insight['campaign_name']
                if '⛔️股市爆料同學會' in Campaign_name:
                    Campaign_name = Campaign_name.replace('⛔️', '')

            # insights/spend得到 "總支出成本"
            if 'spend' in acc_insight:    
                Amount_spent = acc_insight['spend']

            # insights/objective得到 "廣告目標"
            if 'objective' in acc_insight:
                Objective = acc_insight['objective']

            # insights/date_stop得到 "報表終止日期"
            if 'date_stop' in acc_insight:
#                 Reporting_date = acc_insight['date_stop'].strftime("%Y%m%d")
                Reporting_date = datetime.strptime(acc_insight['date_stop'], '%Y-%m-%d').strftime('%Y%m%d')
#                 datetime_object = datetime.strptime(datetime_str, '%m/%d/%y %H:%M:%S')
                
            # insights/actions得到 "軟體下載數/課程購買數"
            if 'actions' in acc_insight:
                for action in acc_insight['actions']:
                    if action['action_type'] == 'mobile_app_install': 
                        Amount_install = action['value']
                    if action['action_type'] == 'purchase':
                        Amount_purchase = action['value']

            # insights/action_values得到 "購買轉換價值"
            if 'action_values' in acc_insight:
                for ac_values in acc_insight['action_values']:
                    if ac_values['action_type'] == 'omni_purchase':
                        Purchase_Conversion_Value = ac_values['value']

            # insights/conversions得到 "訂閱數"
            if 'conversions' in acc_insight:
                for cv in acc_insight['conversions']:
                    if cv['action_type'] == 'subscribe_total':
                        try:
                            Amount_subscribe = cv['7d_click']
                        except:
                            Amount_subscribe = cv['value']

            # insights/conversion_values得到 "訂閱轉換價值"             
            if 'conversion_values' in acc_insight:
                for cv_values in acc_insight['conversion_values']:
                    if cv_values['action_type'] == 'subscribe_total':
                        try:
                            Subscribe_Conversion_Value = cv_values['7d_click']
                        except:
                            Subscribe_Conversion_Value = cv_values['value']
                            
            # 流水號代碼 'FB' + Reproting_date + 000 + order(第幾個資料)
#             Serial_number = 'FB' + str(Reporting_date) + '000' + str(order)
                
            try:
                stuff = [Campaign_name + '\t' + Objective + '\t' + Amount_spent \
                         + '\t' + Amount_install + '\t' + Amount_purchase\
                         + '\t' + Purchase_Conversion_Value + '\t' + Amount_subscribe\
                         + '\t' + Subscribe_Conversion_Value + '\t' + Reporting_date]
                textout.write(','.join(stuff) + '\n')
            except UnicodeEncodeError as e:
                print(e)
                textout.write(' ' + '\n')
            
            except FacebookRequestError as FB_e:
                print(e)
                print(Campaign_name)
            
        print('第{}次'.format(i))
        if (i + 1)%2 == 0:
            time.sleep(300)
        else:
            time.sleep(300)

# df = pd.read_fwf('Test_FB_Ads_Marketing_Data.txt')
# df.to_csv('Test_FB_Ads_Marketing_Data.csv')                                                    

# with open('Test_FB_Ads_Marketing_Data.txt', 'r') as in_file:
#     stripped = (line.decode('utf-8').strip() for line in in_file)
#     print(list(stripped))
#     lines = (line.decode('utf-8').split(",") for line in stripped if line)
#     print(list(lines))
#     with open('Test_FB_Ads_Marketing_Data.csv', 'w', encoding = 'utf-16-le') as out_file:
#         writer = csv.writer(out_file)
#         writer.writerow([
#                     Campaign_name,
#                     Objective,
#                     Amount_spent,
#                     Amount_install, 
#                     Amount_purchase,
#                     Purchase_Conversion_Value,
#                     Amount_subscribe,
#                     Subscribe_Conversion_Value,
#                     Reporting_date,
#                 ])
#         writer.writerows(lines)

# flag確立program完整結束
print('--- %s seconds ---' % (time.time() - run_time))

## 20201214利用Pandas組合(新方法)

In [ ]:
from facebook_business.adobjects.adaccount import AdAccount
from facebook_business.adobjects.adsinsights import AdsInsights
from facebook_business.api import FacebookAdsApi
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
from tqdm.notebook import tqdm
import csv
import time

# 起始值
"""
access_token: 廣告金鑰
ad_account_id: 廣告帳戶
data_back: 往前爬多久的資料(幾個月)
fields: FB_Ads行銷廣告資料
"""
# Initial Values
# 新的金鑰
access_token = 'EAAU5W2nIXuUBAIjps8JaNyhVzjh5mCywvWJDW6tleQXMGEl2xJMdlrfWDZB4wxZCRUU0Ed0FAKXT2acm31ZATt39m3u62ash9SP1La5BHgQOtEIBhCa5prRVDOuzZCPHAWeGPjBWCeZCegS3cmsu8ZBsfvURWFibQByAgGVqC53OHkxZA0pxixoCaXp1fKkLQgZD'
ad_account_id = 'act_132799196821088'
data_back = 12

FacebookAdsApi.init(access_token = access_token)

# 日期計算
def init_time():
    """
    a_week: 一星期
    a_day: 一天
    end_time: 回推月份 - 1個月
    start_time: 回推月份
    """
    a_week = relativedelta(weeks = 1)
    a_day = relativedelta(days = 1)
    
    # 回推月份
    start_time = datetime.now() - data_back*relativedelta(months = 1)
    # 回推月份 - 1個月
    end_time = datetime.now() - (data_back-1)*relativedelta(months = 1)
    return start_time, end_time

# Insight API中的fields資料(控制需要的欄位資料)
fields = [
    'spend',
    'campaign_name',
    'adset_name',
    'campaign_id',
    'actions',
    'objective',
    'action_values',  
    'conversions',
    'conversion_values',
]

# 起始資料放置位置
Campaign_Name = list()
Objective = list()
Amount_Spent = list()
Amount_Install = list()
Amount_Purchase = list()
Purchase_Conversion_Value = list()
Amount_Subscribe = list()
Subscribe_Conversion_Value = list()
Reporting_Date = list()

# 起始時間和結束時間(1次1個月)
start_time, end_time = init_time()

# 紀錄程式跑多久時間
run_time = time.time()
    
# 開始將資料一個月一個月寫入資料庫
for i in tqdm(range(data_back)):
    # Insight API中的fields資料(控制日期條件、資料的層級)
    params = {
        'time_range': {
                    'since': start_time.strftime('%Y-%m-%d'),\
                    'until': end_time.strftime('%Y-%m-%d') 
        }, 
        'level': {'campaign'},
        'time_increment': '1',
        # 手動設定的歸因: 7天點擊後(和廣告預設值有落差)
        'action_attribution_windows': {'7d_click'},
    }
    
    try:
        # 廣告帳號獲取廣告Insights資訊
        acc_insights = AdAccount(ad_account_id).get_insights(
            fields = fields,
            params = params,
        )
    except FacebookRequestError as error:
        print(error)
    
    # 起始時間和結束時間(一次一個月)
    start_time = start_time + relativedelta(months = 1, days = 1)
    end_time = end_time + relativedelta(months = 1)
    
    # 從廣告Inishgts資訊中，清洗、篩選資料
    for acc_insight in acc_insights:     
        campaign_name = ''
        amount_spent = ''
        objective = ''
        amount_subscribe = '' 
        subscribe_conversion_value = ''
        amount_install = '' 
        amount_purchase = ''    
        purchase_conversion_value = ''
        reporting_date = ''

        # insights/campaign_name得到 "產品包名稱"
        if 'campaign_name' in acc_insight:
            campaign_name = acc_insight['campaign_name']
            if '⛔️股市爆料同學會' in campaign_name:
                campaign_name = campaign_name.replace('⛔️', '')

        # insights/spend得到 "總支出成本"
        if 'spend' in acc_insight:    
            amount_spent = acc_insight['spend']

        # insights/objective得到 "廣告目標"
        if 'objective' in acc_insight:
            objective = acc_insight['objective']

        # insights/date_stop得到 "報表終止日期"
        if 'date_stop' in acc_insight:
#                 reporting_date = acc_insight['date_stop']
            reporting_date = datetime.strptime(acc_insight['date_stop'], '%Y-%m-%d').strftime('%Y%m%d')

        # insights/actions得到 "軟體下載數/課程購買數"
        if 'actions' in acc_insight:
            for action in acc_insight['actions']:
                if action['action_type'] == 'mobile_app_install': 
                    amount_install = action['value']
                if action['action_type'] == 'purchase':
                    amount_purchase = action['value']

        # insights/action_values得到 "購買轉換價值"
        if 'action_values' in acc_insight:
            for ac_values in acc_insight['action_values']:
                if ac_values['action_type'] == 'omni_purchase':
                    purchase_conversion_value = ac_values['value']

        # insights/conversions得到 "訂閱數"
        if 'conversions' in acc_insight:
            for cv in acc_insight['conversions']:
                if cv['action_type'] == 'subscribe_total':
                    try:
                        amount_subscribe = cv['7d_click']
                    except:
                        amount_subscribe = cv['value']

        # insights/conversion_values得到 "訂閱轉換價值"             
        if 'conversion_values' in acc_insight:
            for cv_values in acc_insight['conversion_values']:
                if cv_values['action_type'] == 'subscribe_total':
                    try:
                        subscribe_conversion_value = cv_values['7d_click']
                    except:
                        subscribe_conversion_value = cv_values['value']

        # 將資料以List的形式儲存
        try:
            Campaign_Name.append(campaign_name)
            Objective.append(objective)
            Amount_Spent.append(amount_spent)
            Amount_Install.append(amount_install)
            Amount_Purchase.append(amount_purchase)
            Purchase_Conversion_Value.append(purchase_conversion_value)
            Amount_Subscribe.append(amount_subscribe)
            Subscribe_Conversion_Value.append(subscribe_conversion_value)
            Reporting_Date.append(reporting_date)

        except UnicodeEncodeError as e:
            print(e)
        
#     # 顯示錯誤資訊
#     except FacebookRequestError as error:
#         print('流量爆炸? 權限不足?', '\n' ,error)
            
    print('第{}次'.format(i)) 
    time.sleep(100)

# flag確立program完整結束
print('--- %s seconds ---' % (time.time() - run_time))

第0次


In [4]:
import pandas as pd
# 將資料以Dataaframe的方式儲存
raw_data = {'Campaign_Name': Campaign_Name,
         'Objective': Objective,
         'Amount_Spent': Amount_Spent,
         'Amount_Install': Amount_Install,
         'Amount_Purchase': Amount_Purchase,
         'Purchase_Conversion_Value': Purchase_Conversion_Value,
         'Amount_Subscribe': Amount_Subscribe,
         'Subscribe_Conversion_Value': Subscribe_Conversion_Value,
         'Reporting_Date': Reporting_Date}
df = pd.DataFrame.from_dict(raw_data)
df

Campaign_Name     Objective Amount_Spent Amount_Install  \
0            籌碼K線_ 競價下載_行銷活動花費無限制  APP_INSTALLS          204             14   
1                 期貨電子盤_下載_IOS(舊)  APP_INSTALLS           31                  
2                   強棒-應用程式安裝_林恩如  APP_INSTALLS         1004             48   
3            股市爆料同學會_20190617(下載)  APP_INSTALLS          699             75   
4                        恩如講座轉換次數   CONVERSIONS         1000                  
...                           ...           ...          ...            ...   
7112                第三屆大大PM_10秒影片   LINK_CLICKS         1138                  
7113           品牌內容_MB問卷_30天內互動優化   LINK_CLICKS          239                  
7114       20201217股人阿勳_下載_IOS_軟體  APP_INSTALLS          624             22   
7115  20201207_股人阿勳_下載_Android_軟體  APP_INSTALLS          373             13   
7116   股市爆料同學會(非儲理財A)_其他_20201217  APP_INSTALLS          386              8   

     Amount_Purchase Purchase_Conversion_Value Amount_Subscribe  \
0                  1                       360                1   
1                                                                 
2                  3                      7036                    
3                                                                 
4                 16                     76992                    
...              ...                       ...              ...   
7112                                                              
7113                                                              
7114                                                              
7115                                                              
7116                                                              

     Subscribe_Conversion_Value Reporting_Date  
0                           360       20191218  
1                                     20191218  
2                                     20191218  
3                                     20191218  
4                                     20191218  
...                         ...            ...  
7112                                  20201218  
7113                                  20201218  
7114                                  20201218  
7115                                  20201218  
7116                                  20201218  

[7117 rows x 9 columns]

In [ ]:
# 將一些df的重複刪除
df.drop(['Serial_Number'], axis=1)
del df['Serial_Number']
del df['Category']

In [5]:
# 插入新的欄位
import pandas as pd 
import datetime
import numpy as np

# 第幾排插入流水號 & 廣告類別
idx_SN = 0
idx_CA = 10
Serial_Number = []
# 廣告類別
Category = 'FB'

# 增加Serial_Number & Catergory(FB, GOOGL, AAPL)
for order in range(len(df)):
    s_num = str(df['Reporting_Date'][order]) + '000' + str(order)
    Serial_Number.append(int(s_num))

df.insert(loc = idx_SN, column = 'Serial_Number', value = Serial_Number)
df.insert(loc = idx_CA, column = 'Category', value = Category)
df = df.fillna(value = np.nan)
df

Serial_Number                Campaign_Name     Objective Amount_Spent  \
0        201912180000         籌碼K線_ 競價下載_行銷活動花費無限制  APP_INSTALLS          204   
1        201912180001              期貨電子盤_下載_IOS(舊)  APP_INSTALLS           31   
2        201912180002                強棒-應用程式安裝_林恩如  APP_INSTALLS         1004   
3        201912180003         股市爆料同學會_20190617(下載)  APP_INSTALLS          699   
4        201912180004                     恩如講座轉換次數   CONVERSIONS         1000   
...               ...                          ...           ...          ...   
7112  202012180007112                第三屆大大PM_10秒影片   LINK_CLICKS         1138   
7113  202012180007113           品牌內容_MB問卷_30天內互動優化   LINK_CLICKS          239   
7114  202012180007114       20201217股人阿勳_下載_IOS_軟體  APP_INSTALLS          624   
7115  202012180007115  20201207_股人阿勳_下載_Android_軟體  APP_INSTALLS          373   
7116  202012180007116   股市爆料同學會(非儲理財A)_其他_20201217  APP_INSTALLS          386   

     Amount_Install Amount_Purchase Purchase_Conversion_Value  \
0                14               1                       360   
1                                                               
2                48               3                      7036   
3                75                                             
4                                16                     76992   
...             ...             ...                       ...   
7112                                                            
7113                                                            
7114             22                                             
7115             13                                             
7116              8                                             

     Amount_Subscribe Subscribe_Conversion_Value Reporting_Date Category  
0                   1                        360       20191218       FB  
1                                                      20191218       FB  
2                                                      20191218       FB  
3                                                      20191218       FB  
4                                                      20191218       FB  
...               ...                        ...            ...      ...  
7112                                                   20201218       FB  
7113                                                   20201218       FB  
7114                                                   20201218       FB  
7115                                                   20201218       FB  
7116                                                   20201218       FB  

[7117 rows x 11 columns]

In [8]:
for x in df.columns:
    print(x)

Serial_Number
Campaign_Name
Objective
Amount_Spent
Amount_Install
Amount_Purchase
Purchase_Conversion_Value
Amount_Subscribe
Subscribe_Conversion_Value
Reporting_Date
Category


In [ ]:
# 將df內的Data儲存成CSV file
df.to_csv('20201218FBAdsTest.csv', index = False, encoding='utf_8_sig')

In [22]:
import numpy as np
import pandas as pd 

file = r'D:\MIT Python\FB_Ads_Marketing_Data_Scraping\20201218FBAdsTest.csv'
df = pd.read_csv(file)  #匯入資料
df['Reporting_Date'] = df['Reporting_Date'].astype('str') #將資料型態轉為字串,但實際上不轉換寫入SQL時,SQL也會自動處理
df

Serial_Number                Campaign_Name     Objective  \
0        201912180000         籌碼K線_ 競價下載_行銷活動花費無限制  APP_INSTALLS   
1        201912180001              期貨電子盤_下載_IOS(舊)  APP_INSTALLS   
2        201912180002                強棒-應用程式安裝_林恩如  APP_INSTALLS   
3        201912180003         股市爆料同學會_20190617(下載)  APP_INSTALLS   
4        201912180004                     恩如講座轉換次數   CONVERSIONS   
...               ...                          ...           ...   
7112  202012180007112                第三屆大大PM_10秒影片   LINK_CLICKS   
7113  202012180007113           品牌內容_MB問卷_30天內互動優化   LINK_CLICKS   
7114  202012180007114       20201217股人阿勳_下載_IOS_軟體  APP_INSTALLS   
7115  202012180007115  20201207_股人阿勳_下載_Android_軟體  APP_INSTALLS   
7116  202012180007116   股市爆料同學會(非儲理財A)_其他_20201217  APP_INSTALLS   

      Amount_Spent  Amount_Install  Amount_Purchase  \
0              204            14.0              1.0   
1               31             NaN              NaN   
2             1004            48.0              3.0   
3              699            75.0              NaN   
4             1000             NaN             16.0   
...            ...             ...              ...   
7112          1138             NaN              NaN   
7113           239             NaN              NaN   
7114           624            22.0              NaN   
7115           373            13.0              NaN   
7116           386             8.0              NaN   

      Purchase_Conversion_Value  Amount_Subscribe  Subscribe_Conversion_Value  \
0                         360.0               1.0                       360.0   
1                           NaN               NaN                         NaN   
2                        7036.0               NaN                         NaN   
3                           NaN               NaN                         NaN   
4                       76992.0               NaN                         NaN   
...                         ...               ...                         ...   
7112                        NaN               NaN                         NaN   
7113                        NaN               NaN                         NaN   
7114                        NaN               NaN                         NaN   
7115                        NaN               NaN                         NaN   
7116                        NaN               NaN                         NaN   

     Reporting_Date Category  
0          20191218       FB  
1          20191218       FB  
2          20191218       FB  
3          20191218       FB  
4          20191218       FB  
...             ...      ...  
7112       20201218       FB  
7113       20201218       FB  
7114       20201218       FB  
7115       20201218       FB  
7116       20201218       FB  

[7117 rows x 11 columns]

In [ ]:
from tqdm.notebook import tqdm
for col in tqdm(df.columns):
    df[col] = df[col].apply(lambda x: None if x == 'None' else x)
df

In [7]:
# 將df內的Data儲存成CSV file
df.to_csv('20201219FBAdsTest.csv', index = False, encoding='utf_8_sig')

In [49]:
import pandas_profiling as pdp
pdp.ProfileReport(df)

## 輸入資料

In [23]:
import pandas as pd
import numpy as np
import pyodbc

# 連線SQL
DBdata = {'ip':'192.168.99.142', 'db':'CMAPP'}
user142 = 'cmapp'
pwd142 = '0000'
conn_DBdata = pyodbc.connect('DRIVER={SQL Server};SERVER=' + DBdata['ip'] + \
              ';DATABASE=' + DBdata['db'] + ';UID=' + user142 + ';PWD=' + pwd142)
DBdata_cr = conn_DBdata.cursor()

# 參數設定
file = r'D:\MIT Python\FB_Ads_Marketing_Data_Scraping\20201218FBAdsTest.csv'
TableName = 'FB_1221test'
dd1 = '20191201'
dd2 = '20201231'

# 刪除資料
def DelSQL(TableName, dd1, dd2):
    str_query = """
        DELETE
          FROM [CMAPP].[dbo].[{}]
         WHERE Reporting_Date BETWEEN {} AND {}
        """
    print(str_query.format(TableName, dd1, dd2))
    DBdata_cr.execute(str_query.format(TableName, dd1, dd2))
    conn_DBdata.commit()
    
# 寫入資料
def InsertSQL(df, TableName):
    count = 0
    str_query = """
        INSERT INTO [CMAPP].[dbo].[{}]([Serial_Number],[Campaign_Name],[Objective],[Amount_Spent],[Amount_Install],\
        [Amount_Purchase],[Purchase_Conversion_Value],[Amount_Subscribe],[Subscribe_Conversion_Value],[Reporting_Date]\
        ,[Category])VALUES({})
        """
    # 將csv DataFrame每筆資料變成list形式
    insert_data = df.values.tolist()
    print(insert_data)

    for i in range(len(insert_data)):
#         print(str_query.format(TableName, str(insert_data[i]).strip('[]').replace('nan', 'null')))      
        DBdata_cr.execute(str_query.format(TableName, str(insert_data[i]).strip('[]').replace('nan', 'null')))
        conn_DBdata.commit()

        
# 查詢資料
def QuerySQL(TableName):
    str_query = """
        SELECT *
          FROM [CMAPP].[dbo].[{}]
        """
    DBdata_cr.execute(str_query.format(TableName))
    rows = DBdata_cr.fetchall()
    conn_DBdata.commit()
    return rows

# 執行測試
df = pd.read_csv(file)  #匯入資料
df['Reporting_Date'] = df['Reporting_Date'].astype('str') #將資料型態轉為字串,但實際上不轉換寫入SQL時,SQL也會自動處理

# DelSQL(TableName, dd1, dd2) #刪除資料
InsertSQL(df, TableName)    #寫入資料
rows = QuerySQL(TableName)  #查詢寫入資料
print(rows)


#DB斷線
conn_DBdata.close()

[[201912180000, '籌碼K線_ 競價下載_行銷活動花費無限制', 'APP_INSTALLS', 204, 14.0, 1.0, 360.0, 1.0, 360.0, '20191218', 'FB'], [201912180001, '期貨電子盤_下載_IOS(舊)', 'APP_INSTALLS', 31, nan, nan, nan, nan, nan, '20191218', 'FB'], [201912180002, '強棒-應用程式安裝_林恩如', 'APP_INSTALLS', 1004, 48.0, 3.0, 7036.0, nan, nan, '20191218', 'FB'], [201912180003, '股市爆料同學會_20190617(下載)', 'APP_INSTALLS', 699, 75.0, nan, nan, nan, nan, '20191218', 'FB'], [201912180004, '恩如講座轉換次數', 'CONVERSIONS', 1000, nan, 16.0, 76992.0, nan, nan, '20191218', 'FB'], [201912180005, '權證小哥_講座_轉換次數(購買)', 'CONVERSIONS', 1209, nan, 19.0, 38288.0, nan, nan, '20191218', 'FB'], [201912180006, '正在查看的籌碼K線下載細項', 'APP_INSTALLS', 102, 8.0, nan, nan, nan, nan, '20191218', 'FB'], [201912180007, '丹尼爾-應用程式安裝', 'APP_INSTALLS', 694, 39.0, nan, nan, nan, nan, '20191218', 'FB'], [201912180008, '20200923_籌碼K線_最後衝刺_iOS', 'APP_INSTALLS', 6078, 170.0, 1.0, 3771.0, 2.0, 3650.0, '20191218', 'FB'], [201912180009, '大大工程師-第六屆招生', 'LINK_CLICKS', 950, nan, nan, nan, nan, nan, '

## 如何提取出時間?

In [10]:
import pandas as pd
import numpy as np
import pyodbc

# 連線SQL
DBdata = {'ip':'192.168.99.142', 'db':'CMAPP'}
user142 = 'cmapp'
pwd142 = '0000'
conn_DBdata = pyodbc.connect('DRIVER={SQL Server};SERVER=' + DBdata['ip'] + \
              ';DATABASE=' + DBdata['db'] + ';UID=' + user142 + ';PWD=' + pwd142)
DBdata_cr = conn_DBdata.cursor()
TableName = 'FB_1214test'

# 提取資料
def query_timeSQL(TableName):
    select_query = """
        SELECT MAX("Reporting_Date")
        FROM  [CMAPP].[dbo].[{}]
        """
    print(select_query.format(TableName))
    DBdata_cr.execute(select_query.format(TableName))
    dates = DBdata_cr.fetchall()
    conn_DBdata.commit()
    return dates
    
date = query_timeSQL(TableName)  
print(date, '\n')
# object 沒有strip
# print(str(num).strip('[]').strip('()').strip("''").strip(","), '\n')
# print(str(num).strip('[]').strip('()'), '\n')
qqq = [k for k in str(date).strip('[]').strip('()').split(',')]
# qqq = [k for k in str(num)]

print(qqq, '\n')
for i in qqq:
#     print(i, '\n')
    print(i.strip().strip('Decimal').strip("'"), '\n')
    x = i.strip().strip('Decimal').strip("'")
    
    try:
        larggest_date = float(x)
        larggest_date = int(larggest_date)
        print('This is: ', larggest_date)
        print(type(larggest_date), '\n')
        print(larggest_date + 10)
    except ValueError as e_reporting_date:
        print(e_reporting_date)
    

#DB斷線
conn_DBdata.close()


        SELECT MAX("Reporting_Date")
        FROM  [CMAPP].[dbo].[FB_1214test]
        
[('20201218', )] 

["'20201218'", ' '] 

20201218 

This is:  20201218
<class 'int'> 

20201228
 

could not convert string to float: 


## 如何提取流水號?

In [5]:
import pandas as pd
import numpy as np
import pyodbc
import logging 

logging.basicConfig(level = logging.DEBUG)

# 連線SQL
DBdata = {'ip':'192.168.99.142', 'db':'CMAPP'}
user142 = 'cmapp'
pwd142 = '0000'
conn_DBdata = pyodbc.connect('DRIVER={SQL Server};SERVER=' + DBdata['ip'] + \
              ';DATABASE=' + DBdata['db'] + ';UID=' + user142 + ';PWD=' + pwd142)
DBdata_cr = conn_DBdata.cursor()
TableName = 'FB_1214test'
e_serial_number = []

# 提取流水號
def SelecSQL(TableName):
    select_query = """
        SELECT MAX("Serial_Number")
        FROM  [CMAPP].[dbo].[{}]
        """
    print(select_query.format(TableName))
    DBdata_cr.execute(select_query.format(TableName))
    nums = DBdata_cr.fetchall()
    conn_DBdata.commit()
    return nums

# 更新流水號
def Update_Serial_NumberSQL(para):
    qqq = [k for k in str(para).strip('[]').strip('()').split(',')]
    
    for i in qqq:
        x = i.strip().strip('Decimal').strip('()').strip("'")
        try:
            larggest_serial_number = int(float(x))
        except:
            e_serial_number = logging.error("Catch an exception.", exc_info=True)
#         except ValueError as e_serial_number:
#             e_serial_number = str(e_serial_number)
#             print(e_serial_number)
#             e_serial_number = logging.debug('debug message')
    return larggest_serial_number, e_serial_number

num = SelecSQL(TableName)  
larggest_SN, e_SN = Update_Serial_NumberSQL(num)

print(larggest_SN, '\n')
# print(e_SN, '\n')
print('Success')

#DB斷線
conn_DBdata.close()

ERROR:root:Catch an exception.
Traceback (most recent call last):
  File "<ipython-input-5-2034e6f256fc>", line 39, in Update_Serial_NumberSQL
    larggest_serial_number = int(float(x))
ValueError: could not convert string to float: 



        SELECT MAX("Serial_Number")
        FROM  [CMAPP].[dbo].[FB_1214test]
        
202012180007116 

Success


## 刪除1個月資料，順序寫入新的流水號

In [34]:
import pandas as pd
import numpy as np
import pyodbc
from datetime import datetime 
from dateutil.relativedelta import relativedelta

# 連線SQL
DBdata = {'ip':'192.168.99.142', 'db':'CMAPP'}
user142 = 'cmapp'
pwd142 = '0000'
conn_DBdata = pyodbc.connect('DRIVER={SQL Server};SERVER=' + DBdata['ip'] + \
              ';DATABASE=' + DBdata['db'] + ';UID=' + user142 + ';PWD=' + pwd142)
DBdata_cr = conn_DBdata.cursor()

# 參數設定
file = r'D:\MIT Python\FB_Ads_Marketing_Data_Scraping\20201218FBAdsTest.csv'
TableName = 'FB_1221test'

# 將日期回轉一個月並
def Uppdate_date(date):
    reporting_date = datetime.strptime(str(date), '%Y%m%d')
    reporting_date = reporting_date.date() - relativedelta(months = 1)
    print(reporting_date.strftime('%Y-%m-%d'))
    return reporting_date
    
    
reporting_date = Uppdate_date(larggest_date)
dd1 = reporting_date.strftime('%Y%m%d')
dd2 = datetime.now().strftime('%Y%m%d')

print(dd1, dd2)
# reporting_date = datetime.strptime(acc_insight['date_stop'], '%Y-%m-%d').strftime('%Y%m%d')

# 刪除資料
def DelSQL(TableName, dd1, dd2):
    str_query = """
        DELETE
          FROM [CMAPP].[dbo].[{}]
         WHERE Reporting_Date BETWEEN {} AND {}
        """
    print(str_query.format(TableName, dd1, dd2))
    DBdata_cr.execute(str_query.format(TableName, dd1, dd2))
    conn_DBdata.commit()

2020-11-18
20201118 20201221


## 總體測試(洗掉過去1個月的資料，並寫入新的一個月資料)

In [3]:
import pandas as pd
import numpy as np
import pyodbc
import logging 
from datetime import datetime 
from dateutil.relativedelta import relativedelta

# 連線SQL
DBdata = {'ip':'192.168.99.142', 'db':'CMAPP'}
user142 = 'cmapp'
pwd142 = '0000'
conn_DBdata = pyodbc.connect('DRIVER={SQL Server};SERVER=' + DBdata['ip'] + \
              ';DATABASE=' + DBdata['db'] + ';UID=' + user142 + ';PWD=' + pwd142)
DBdata_cr = conn_DBdata.cursor()
TableName = 'FB_1221test'

# 提取流水號
def Query_Serial_NumberSQL(TableName):
    select_query = """
        SELECT MAX("Serial_Number")
        FROM [CMAPP].[dbo].[{}]
        """
    print(select_query.format(TableName))
    DBdata_cr.execute(select_query.format(TableName))
    nums = DBdata_cr.fetchall()
    conn_DBdata.commit()
    return nums

# 清洗流水號(Serial_Number)欄位，並更新
def Update_Serial_NumberSQL(para):
    qqq = [k for k in str(para).strip('[]').strip('()').split(',')]
    
    for i in qqq:
        x = i.strip().strip('Decimal').strip('()').strip("'")
        try:
            new_serial_number = int(float(x))
        except:
            e_serial_number = logging.error("Catch an exception.", exc_info=True)
#         except ValueError as e_serial_number:
#             e_serial_number = str(e_serial_number)
#             print(e_serial_number)
#             e_serial_number = logging.debug('debug message')
    return new_serial_number

# 提取時間(Reporting_time)行列
def query_timeSQL(TableName):
    select_query = """
        SELECT MAX("Reporting_Date")
        FROM [CMAPP].[dbo].[{}]
        """
    print(select_query.format(TableName))
    DBdata_cr.execute(select_query.format(TableName))
    dates = DBdata_cr.fetchall()
    conn_DBdata.commit()
    # Get the latest time 
    return dates

# 清洗時間(Reporting_time)欄位，並更新
def clean_update_time(para):
    qqq = [k for k in str(para).strip('[]').strip('()').split(',')]
    for i in qqq:
        print(i.strip().strip('Decimal').strip("'"), '\n')
        x = i.strip().strip('Decimal').strip("'")

        try:
            larggest_date = float(x)
            larggest_date = int(larggest_date)
#             print('This is: ', larggest_date)
#             print(type(larggest_date), '\n')
#             print(larggest_date + 10)
        except ValueError as e_reporting_date:
            print(e_reporting_date)
    return larggest_date
        
# 回溯1個月前的時間
def Uppdate_date(date):
    reporting_date = datetime.strptime(str(date), '%Y%m%d')
    reporting_date = reporting_date.date() - relativedelta(months = 1)
    print(reporting_date.strftime('%Y-%m-%d'))
    return reporting_date

# 刪除資料
def DelSQL(TableName, start_time, end_time):
    str_query = """
        DELETE
          FROM [CMAPP].[dbo].[{}]
         WHERE Reporting_Date BETWEEN {} AND {}
        """
    print(str_query.format(TableName, start_time, end_time))
    DBdata_cr.execute(str_query.format(TableName, start_time, end_time))
    conn_DBdata.commit()   
    
# 寫入資料
def InsertSQL(df, TableName):
    str_query = """
        INSERT INTO [CMAPP].[dbo].[{}]([Serial_Number],[Campaign_Name],[Objective],[Amount_Spent],[Amount_Install],\
        [Amount_Purchase],[Purchase_Conversion_Value],[Amount_Subscribe],[Subscribe_Conversion_Value],[Reporting_Date]\
        ,[Category])VALUES({})
        """
    # 將csv DataFrame每筆資料變成list形式
    insert_data = df.values.tolist()
    print(insert_data)

    for i in range(len(insert_data)):
#         print(str_query.format(TableName, str(insert_data[i]).strip('[]').replace('nan', 'null')))      
        DBdata_cr.execute(str_query.format(TableName, str(insert_data[i]).strip('[]').replace('nan', 'null')))
        conn_DBdata.commit() 
        
# 提取SQL時間(Reporting_time)行列
query_time = query_timeSQL(TableName)  
# 清洗時間(Reporting_time)欄位
clean_time = clean_update_time(query_time)  
print(clean_time)
# 將日期回轉一個月
back_time_month = Uppdate_date(clean_time)
print(back_time_month)
# 提取流水號
Seri_num = Query_Serial_NumberSQL(TableName)
# 清洗流水號(Serial_Number)欄位，並更新
clean_num = Update_Serial_NumberSQL(Seri_num)

# 日期得到
start_time = back_time_month.strftime('%Y%m%d')
end_time = datetime.now().strftime('%Y%m%d')
print(start_time)
#刪除資料
# DelSQL(TableName, start_time, end_time)

ERROR:root:Catch an exception.
Traceback (most recent call last):
  File "<ipython-input-3-5e5a01ec62c1>", line 36, in Update_Serial_NumberSQL
    new_serial_number = int(float(x))
ValueError: could not convert string to float: 



        SELECT MAX("Reporting_Date")
        FROM [CMAPP].[dbo].[FB_1221test]
        
20201016 

 

could not convert string to float: 
20201016
2020-09-16
2020-09-16

        SELECT MAX("Serial_Number")
        FROM [CMAPP].[dbo].[FB_1221test]
        
20200916


## 爬取資料

In [2]:
from facebook_business.adobjects.adaccount import AdAccount
from facebook_business.adobjects.adsinsights import AdsInsights
from facebook_business.api import FacebookAdsApi
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
from tqdm.notebook import tqdm
import csv
import time

# 起始值
"""
access_token: 廣告金鑰
ad_account_id: 廣告帳戶
data_back: 往前爬多久的資料(幾個月)
fields: FB_Ads行銷廣告資料
"""
# Initial Values
# 新的金鑰
access_token = 'EAAU5W2nIXuUBAIjps8JaNyhVzjh5mCywvWJDW6tleQXMGEl2xJMdlrfWDZB4wxZCRUU0Ed0FAKXT2acm31ZATt39m3u62ash9SP1La5BHgQOtEIBhCa5prRVDOuzZCPHAWeGPjBWCeZCegS3cmsu8ZBsfvURWFibQByAgGVqC53OHkxZA0pxixoCaXp1fKkLQgZD'
ad_account_id = 'act_132799196821088'
data_back = 1

FacebookAdsApi.init(access_token = access_token)

# # 日期計算
# def init_time():
#     """
#     a_week: 一星期
#     a_day: 一天
#     end_time: 回推月份 - 1個月
#     start_time: 回推月份
#     """
#     a_week = relativedelta(weeks = 1)
#     a_day = relativedelta(days = 1)
    
#     # 回推月份
#     start_time = datetime.now() - data_back*relativedelta(months = 1)
#     # 回推月份 - 1個月
#     end_time = datetime.now() - (data_back-1)*relativedelta(months = 1)
#     return start_time, end_time

# Insight API中的fields資料(控制需要的欄位資料)
fields = [
    'spend',
    'campaign_name',
    'adset_name',
    'campaign_id',
    'actions',
    'objective',
    'action_values',  
    'conversions',
    'conversion_values',
]

# 起始資料放置位置
Campaign_Name = list()
Objective = list()
Amount_Spent = list()
Amount_Install = list()
Amount_Purchase = list()
Purchase_Conversion_Value = list()
Amount_Subscribe = list()
Subscribe_Conversion_Value = list()
Reporting_Date = list()

# 起始時間和結束時間(1次1個月)
# start_time, end_time = init_time()

# 紀錄程式跑多久時間
run_time = time.time()
    
# 開始將資料一個月一個月寫入資料庫
for i in range(data_back):
    # Insight API中的fields資料(控制日期條件、資料的層級)
    params = {
        'time_range': {
                    # 時間的值在上一個cell 
            
                    'since': datetime.strptime(start_time, '%Y%m%d').strftime('%Y-%m-%d'),\
                    'until': datetime.strptime(end_time, '%Y%m%d').strftime('%Y-%m-%d')
#                     'since': start_time.strftime('%Y-%m-%d'),\
#                     'until': end_time.strftime('%Y-%m-%d') 
        }, 
        'level': {'campaign'},
        'time_increment': '1',
        # 手動設定的歸因: 7天點擊後(和廣告預設值有落差)
        'action_attribution_windows': {'7d_click'},
    }
    
    try:
        # 廣告帳號獲取廣告Insights資訊
        acc_insights = AdAccount(ad_account_id).get_insights(
            fields = fields,
            params = params,
        )
    except FacebookRequestError as error:
        print(error)
    
    # 起始時間和結束時間(一次一個月)
#     start_time = start_time + relativedelta(months = 1, days = 1)
#     end_time = end_time + relativedelta(months = 1)
    
    # 從廣告Inishgts資訊中，清洗、篩選資料
    for acc_insight in acc_insights:     
        campaign_name = ''
        amount_spent = ''
        objective = ''
        amount_subscribe = '' 
        subscribe_conversion_value = ''
        amount_install = '' 
        amount_purchase = ''    
        purchase_conversion_value = ''
        reporting_date = ''

        # insights/campaign_name得到 "產品包名稱"
        if 'campaign_name' in acc_insight:
            campaign_name = acc_insight['campaign_name']
            if '⛔️股市爆料同學會' in campaign_name:
                campaign_name = campaign_name.replace('⛔️', '')

        # insights/spend得到 "總支出成本"
        if 'spend' in acc_insight:    
            amount_spent = acc_insight['spend']

        # insights/objective得到 "廣告目標"
        if 'objective' in acc_insight:
            objective = acc_insight['objective']

        # insights/date_stop得到 "報表終止日期"
        if 'date_stop' in acc_insight:
#                 reporting_date = acc_insight['date_stop']
            reporting_date = datetime.strptime(acc_insight['date_stop'], '%Y-%m-%d').strftime('%Y%m%d')

        # insights/actions得到 "軟體下載數/課程購買數"
        if 'actions' in acc_insight:
            for action in acc_insight['actions']:
                if action['action_type'] == 'mobile_app_install': 
                    amount_install = action['value']
                if action['action_type'] == 'purchase':
                    amount_purchase = action['value']

        # insights/action_values得到 "購買轉換價值"
        if 'action_values' in acc_insight:
            for ac_values in acc_insight['action_values']:
                if ac_values['action_type'] == 'omni_purchase':
                    purchase_conversion_value = ac_values['value']

        # insights/conversions得到 "訂閱數"
        if 'conversions' in acc_insight:
            for cv in acc_insight['conversions']:
                if cv['action_type'] == 'subscribe_total':
                    try:
                        amount_subscribe = cv['7d_click']
                    except:
                        amount_subscribe = cv['value']

        # insights/conversion_values得到 "訂閱轉換價值"             
        if 'conversion_values' in acc_insight:
            for cv_values in acc_insight['conversion_values']:
                if cv_values['action_type'] == 'subscribe_total':
                    try:
                        subscribe_conversion_value = cv_values['7d_click']
                    except:
                        subscribe_conversion_value = cv_values['value']

        # 將資料以List的形式儲存
        try:
            Campaign_Name.append(campaign_name)
            Objective.append(objective)
            Amount_Spent.append(amount_spent)
            Amount_Install.append(amount_install)
            Amount_Purchase.append(amount_purchase)
            Purchase_Conversion_Value.append(purchase_conversion_value)
            Amount_Subscribe.append(amount_subscribe)
            Subscribe_Conversion_Value.append(subscribe_conversion_value)
            Reporting_Date.append(reporting_date)

        except UnicodeEncodeError as e:
            print(e)
        
#     # 顯示錯誤資訊
#     except FacebookRequestError as error:
#         print('流量爆炸? 權限不足?', '\n' ,error)
            
    print('第{}次'.format(i)) 
    time.sleep(100)

# flag確立program完整結束
print('--- %s seconds ---' % (time.time() - run_time))

D:\Anaconda_JupyterNotebook\lib\site-packages\facebook_business\utils\api_utils.py:30: UserWarning: value of level might not be compatible.  Expect level_enum;  got <class 'set'>
  warnings.warn(message)
D:\Anaconda_JupyterNotebook\lib\site-packages\facebook_business\utils\api_utils.py:30: UserWarning: value of action_attribution_windows might not be compatible.  Expect list<action_attribution_windows_enum>;  got <class 'set'>
  warnings.warn(message)


NameError: name 'FacebookRequestError' is not defined

In [ ]:
import pandas as pd
# 將資料以Dataaframe的方式儲存
raw_data = {'Campaign_Name': Campaign_Name,
         'Objective': Objective,
         'Amount_Spent': Amount_Spent,
         'Amount_Install': Amount_Install,
         'Amount_Purchase': Amount_Purchase,
         'Purchase_Conversion_Value': Purchase_Conversion_Value,
         'Amount_Subscribe': Amount_Subscribe,
         'Subscribe_Conversion_Value': Subscribe_Conversion_Value,
         'Reporting_Date': Reporting_Date}
df = pd.DataFrame.from_dict(raw_data)
df

In [ ]:
# 插入新的欄位
import pandas as pd 
import datetime
import numpy as np

# 第幾排插入流水號 & 廣告類別
idx_SN = 0
idx_CA = 10
Serial_Number = []
# 廣告類別
Category = 'FB'

# 增加Serial_Number & Catergory(FB, GOOGL, AAPL)
for order in range(len(df)):
    s_num = int(clean_num) + order
    Serial_Number.append(int(s_num))

df.insert(loc = idx_SN, column = 'Serial_Number', value = Serial_Number)
df.insert(loc = idx_CA, column = 'Category', value = Category)
df = df.fillna(value = np.nan)
df

In [ ]:
InsertSQL(df, TableName)

# 關閉 DB
conn_DBdata.close()

In [ ]:
file = r'D:\MIT Python\FB_Ads_Marketing_Data_Scraping\20201214FBAdsTest.csv'
# 執行測試
df = pd.read_csv(file)  #匯入資料
df['Reporting_Date'] = df['Reporting_Date'].astype('str') #將資料型態轉為字串,但實際上不轉換寫入SQL時,SQL也會自動處理

insert_data = df.values.tolist()
count = 0

# a = [str(insert_data[0]).strip('[]').replace('None', 'null')]
# print(a)

for i in range(len(insert_data)):
    print('這是i: ', i)
    # 先將insert_data內的None，轉變成null，並存成list
    a = [str(insert_data[i]).strip('[]').replace('None', 'null')]
#     print(a)
    # 因list內只有一個element，將原element透過","，切成11個elements，存成list(list)
    qqq = [k.split(',') for k in a]
    print(qqq)
    
    count = 0
    index = 0
    for j in qqq[0]:
        print(j.strip(' '))
        if j.strip(' ') == "'null'":
            qqq[0][index] = j.strip(' ').replace("'", "")
            print('幹你娘')
#             print(qqq[0][index])
            print(j.strip(' ').replace("'", ""))
        index += 1
    count += 1
#     print(qqq)    

    if count >= 10:
        break
    str_query = """
        INSERT INTO [CMAPP].[dbo].[{}]([Serial_Number],[Campaign_Name],[Objective],[Amount_Spent],[Amount_Install],\
        [Amount_Purchase],[Purchase_Conversion_Value],[Amount_Subscribe],[Subscribe_Conversion_Value],[Reporting_Date]\
        ,[Category])VALUES ({})
        """
    print(str_query.format(TableName, str(qqq).strip('[]').replace('"', '')))
    print(str_query.format(TableName, qqq))

#             print(j.strip(' ').replace("'", ""))

#     print(insert_data[i])
#         str(insert_data[i]).replace('None', 'null')
        
#         if insert_data[i][j] == 'null':
#             print(yes)
#             insert_data[i][j] = insert_data[i][j].replace("'", "")
# print(a)

# str_query = """
#         INSERT INTO [CMAPP].[dbo].[{}]([Serial_Number],[Campaign_Name],[Objective],[Amount_Spent],[Amount_Install],\
#         [Amount_Purchase],[Purchase_Conversion_Value],[Amount_Subscribe],[Subscribe_Conversion_Value],[Reporting_Date]\
#         ,[Category])VALUES ({})
#         """
# print(str_query.format(TableName, qqq))